# [Nicholas Yim, Aseef Durrani]
# Dataset \#3 - Energy Consumption Clustering
---

In [171]:
import pandas as pd
import numpy as np
import plotly.express as px

# **A. Load and Explore Dataset**

In [172]:
# Load the dataset
data = pd.read_csv("../datasets/energy/owid-energy-data.csv")

# Preview of the dataset
print("Preview of the dataset:")
print(data.head())

# Number of samples and features
print("\nDataset shape (samples, features):", data.shape)

Preview of the dataset:
         country  year iso_code  population  gdp  biofuel_cons_change_pct  \
0  ASEAN (Ember)  2000      NaN         NaN  NaN                      NaN   
1  ASEAN (Ember)  2001      NaN         NaN  NaN                      NaN   
2  ASEAN (Ember)  2002      NaN         NaN  NaN                      NaN   
3  ASEAN (Ember)  2003      NaN         NaN  NaN                      NaN   
4  ASEAN (Ember)  2004      NaN         NaN  NaN                      NaN   

   biofuel_cons_change_twh  biofuel_cons_per_capita  biofuel_consumption  \
0                      NaN                      NaN                  NaN   
1                      NaN                      NaN                  NaN   
2                      NaN                      NaN                  NaN   
3                      NaN                      NaN                  NaN   
4                      NaN                      NaN                  NaN   

   biofuel_elec_per_capita  ...  solar_share_elec  solar

In [173]:
# Load the codebook
codebook = pd.read_csv("../datasets/energy/owid-energy-codebook.csv")
index_cols = ["country", "year", "iso_code"]
deprecated_countries = ["burma", "macedonia", "swaziland", "czech republic"]

# Validation Functions
def validate_columns_in_codebook(data, codebook):
    missing_in_codebook = data.columns.difference(codebook["column"])
    if not missing_in_codebook.empty:
        print(f"Columns not in codebook: {missing_in_codebook.tolist()}")

def validate_codebook_columns_in_data(data, codebook):
    missing_in_data = set(codebook["column"]) - set(data.columns)
    if missing_in_data:
        print(f"Codebook columns missing in data: {list(missing_in_data)}")

def validate_column_whitespace(data):
    columns_with_space = [col for col in data.columns if " " in col]
    if columns_with_space:
        print(f"Columns with whitespace: {columns_with_space}")

def validate_column_case(data):
    non_lowercase_columns = [col for col in data.columns if col != col.lower()]
    if non_lowercase_columns:
        print(f"Columns with uppercase characters: {non_lowercase_columns}")

def validate_non_nan_rows(data, index_cols):
    nan_rows = data.drop(columns=index_cols, errors="ignore").isnull().all(axis=1)
    if nan_rows.any():
        print(f"Rows with all NaN values: {nan_rows.sum()}")

def validate_deprecated_country_names(data, deprecated_countries):
    countries_in_data = data["country"].str.lower().unique()
    for country in deprecated_countries:
        if country in countries_in_data:
            print(f"Deprecated country found: {country}")

# Run all validations
print("\nValidating dataset...")
validate_columns_in_codebook(data, codebook)
validate_codebook_columns_in_data(data, codebook)
validate_column_whitespace(data)
validate_column_case(data)
validate_non_nan_rows(data, index_cols)
validate_deprecated_country_names(data, deprecated_countries)
print("Dataset validation complete.")


Validating dataset...
Dataset validation complete.


In [174]:
# Fraction of missing values
missing_fraction = data.isnull().sum() / len(data)
missing_fraction = missing_fraction[missing_fraction > 0].sort_values(ascending=False)

# Display missing values
print("\nColumns with missing values and their fractions:")
print(missing_fraction)

# Visualize missing values
missing_df = missing_fraction.reset_index()
missing_df.columns = ["Feature", "Missing Fraction"]
fig = px.bar(
    missing_df,
    x="Feature",
    y="Missing Fraction",
    title="Fraction of Missing Values per Feature",
    labels={"Feature": "Feature", "Missing Fraction": "Missing Fraction"},
)
fig.update_layout(xaxis=dict(tickangle=45), width=900)
fig.show()


Columns with missing values and their fractions:
biofuel_cons_change_pct    0.917202
solar_cons_change_pct      0.897717
biofuel_cons_per_capita    0.889969
nuclear_cons_change_pct    0.886209
wind_cons_change_pct       0.885017
                             ...   
iso_code                   0.229232
gas_production             0.227994
oil_prod_change_twh        0.210389
oil_production             0.198606
population                 0.154273
Length: 128, dtype: float64


In [175]:
# Identify and analyze categorical variables
categorical_variables = data.select_dtypes(include=["object"]).columns
print("\nCategorical Variables:")
print(categorical_variables.tolist())

# Visualize count of unique countries
fig = px.bar(
    x=data["country"].value_counts().index,
    y=data["country"].value_counts().values,
    title="Number of Records per Country",
    labels={"x": "Country", "y": "Number of Records"},
)
fig.update_layout(width=1000, xaxis=dict(tickangle=45))
fig.show()


Categorical Variables:
['country', 'iso_code']


In [176]:
# Summary statistics for numerical features
print("\nSummary statistics for numerical features:")
print(data.describe())

# Normalize numerical features manually for better visualization
numerical_features = data.select_dtypes(include=[np.number]).columns
normalized_data = data[numerical_features].apply(lambda x: (x - x.min()) / (x.max() - x.min()), axis=0)

# Create a summary DataFrame for normalized statistics
summary_df = normalized_data.describe().reset_index().melt(id_vars="index")

# Improved Plotly scatter plot with clearer y-axis
fig = px.scatter(
    summary_df,
    x="variable",
    y="value",
    color="index",
    title="Summary Statistics for Numerical Features (Normalized)",
    labels={"variable": "Feature", "value": "Normalized Value", "index": "Statistic"},
)
fig.update_layout(
    xaxis=dict(tickangle=45, title="Features"),
    yaxis=dict(title="Normalized Values (0 to 1)", range=[0, 1]),
    width=1200,
    height=600,
    legend_title="Statistic",
    template="plotly_white",  # Add a clean background style
    title_font=dict(size=20),  # Enhance title size
)
fig.show()


Summary statistics for numerical features:
               year    population           gdp  biofuel_cons_change_pct  \
count  21812.000000  1.844700e+04  1.177500e+04              1806.000000   
mean    1974.195718  1.054051e+08  4.260596e+11                45.489759   
std       35.342860  4.665375e+08  3.508591e+12               266.131064   
min     1900.000000  1.833000e+03  1.642060e+08              -100.000000   
25%     1946.000000  1.714291e+06  1.438637e+10                -0.500000   
50%     1984.000000  6.998022e+06  4.393385e+10                 8.189000   
75%     2004.000000  2.571993e+07  1.830838e+11                26.550000   
max     2023.000000  8.045311e+09  1.301126e+14              5659.328000   

       biofuel_cons_change_twh  biofuel_cons_per_capita  biofuel_consumption  \
count              2796.000000              2400.000000          2876.000000   
mean                  2.867027               136.600523            39.082519   
std                  10.692769 

In [177]:
# Histograms for selected features
selected_features = [
    "population", "gdp", "energy_per_capita", 
    "fossil_share_energy", "renewables_share_energy"
]

# Plot histograms for selected features
for feature in selected_features:
    fig = px.histogram(
        data, 
        x=feature, 
        nbins=20, 
        title=f"Histogram of {feature}",
        labels={feature: feature, "count": "Frequency"},
    )
    fig.show()

In [178]:
# Distribution of records over years
fig = px.histogram(
    data, 
    x="year", 
    title="Distribution of Records Over Years", 
    labels={"year": "Year", "count": "Frequency"},
    nbins=20,
)
fig.update_layout(bargap=0.1)
fig.show()

# **Dataset Exploration**

## Overview
This notebook explores the **Our World in Data Energy Consumption Dataset** by loading the data, validating its structure, and visualizing key aspects. The exploration focuses on understanding the dataset's distribution, identifying missing values, and summarizing numerical features to prepare it for further analysis.

---

### **Steps Performed**

#### **1. Dataset Validation**
- **Purpose**: To ensure the dataset is clean, consistent, and ready for analysis.
- **Validation Checks**:
  - Columns in the dataset match the codebook.
  - All columns in the dataset are lowercase and do not contain whitespace.
  - Deprecated country names (e.g., "Swaziland", "Burma") are not present.
  - Rows contain at least one non-NaN value.
- **Outcome**: No critical issues were identified during validation, ensuring the dataset's consistency.

---

#### **2. Missing Value Analysis**
- **Purpose**: To identify features with missing data for potential cleaning or imputation.
- **Key Findings**:
  - Many columns have a high fraction of missing values (>80%).
  - Missing data is visualized using a bar chart for clarity.

---

#### **3. Dataset Statistics**
- **Purpose**: To summarize numerical features and provide an overview of data ranges.
- **Key Insights**:
  - Features such as `population`, `gdp`, and `energy_per_capita` exhibit large variability.
  - Summary statistics (mean, median, std, min, max) help in understanding data distributions.

---

#### **4. Feature Exploration**
- **Purpose**: To visualize key features and their distributions.
- **Steps**:
  - Histograms are plotted for selected features (`population`, `gdp`, `energy_per_capita`, `fossil_share_energy`, `renewables_share_energy`) to reveal their distributions.
  - Insights on feature skewness or sparsity are derived.
  - The distribution of records over years and by country is visualized to understand temporal and geographical coverage.

---

### **Visualizations and Insights**
1. **Missing Value Distribution**:
   - A bar chart highlights columns with the highest fraction of missing values.
   - Columns with >80% missing values may need to be dropped or imputed.

2. **Numerical Feature Summary**:
   - A scatter plot visualizes normalized summary statistics (mean, min, max, etc.) for all numerical features.
   - Reveals potential outliers or irregular ranges.

3. **Histograms**:
   - Histograms for key features such as `population` and `energy_per_capita` reveal significant skewness, indicating the presence of outliers or imbalanced distributions.

4. **Temporal Analysis**:
   - The number of records per year is consistent, with a drop in recent years indicating incomplete data for later periods.

5. **Geographical Analysis**:
   - The distribution of records across countries is imbalanced, with certain countries contributing more data than others.

---

## Insights
- The dataset requires careful handling of missing values and imbalances in temporal and geographical coverage.
- Visualizations provide a clear understanding of key features and their distributions, helping guide subsequent clustering or modeling efforts.

# **B. Pre-Processing of Dataset**

In [179]:
# Filter data from the year 2000 to 2021
data_2002_2021 = data[(data["year"] >= 2002) & (data["year"] <= 2021)].copy()

print(f"Data filtered to include records from the year 2002 to 2021. New shape: {data_2002_2021.shape}")

Data filtered to include records from the year 2002 to 2021. New shape: (5681, 130)


In [180]:
# List of continents and keywords to exclude
exclude_keywords = [
    "income", "middle east", "middle africa", "oecd", "opec", 
    "persian gulf", "south and central america", "asean", "wake island",
    "pacific islands", "territories", "western africa", "world", "g7", "g20", "cis", 
    "africa", "antarctica", "asia", "europe", "north america", "south america", "oceania",
    "latin america", "eastern africa", "africa (ei)", "(EIA)", "(Shift)", "Serbia and Montenegro", "Tuvalu", "Micronesia (country)", "Northern Mariana Islands",
    "Micronesia (country)", "Curacao", "Netherlands Antilles","East Timor","Central America", "Micronesia", "South Sudan", "Montenegro", "Western Sahara", "Niue"
]

# Convert keywords to lowercase for case-insensitive matching
exclude_keywords_lower = [kw.lower() for kw in exclude_keywords]

# Filter out unwanted regions, continents, and specific cases
data_2002_2021 = data_2002_2021[
    ~(
        data_2002_2021["country"].str.lower().str.contains("|".join(exclude_keywords_lower), na=False) |
        (data_2002_2021["country"].str.strip().str.lower() == "africa")  # Exclude exact "Africa"
    )
]

print(f"Data shape after filtering excluded regions/categories: {data_2002_2021.shape}")

# Retain only the latest record for each country (based on the assumption that 'year' exists and is chronological)
filtered_data_unique = (
    data_2002_2021.sort_values("year", ascending=False)
    .drop_duplicates(subset=["country"], keep="first")
)

# Retain only the latest record for each country (based on the assumption that 'year' exists and is chronological)
filtered_data_unique2 = (
    data_2002_2021.sort_values("year", ascending=False)
    .drop_duplicates(subset=["country"], keep="last")
)

print("\n\n\nFiltered data unique 2: ", data_2002_2021.sort_values("year", ascending=False)
    .drop_duplicates(subset=["country"], keep="last"))

# Save the resulting dataset to a CSV file
filtered_data_unique.to_csv("filtered_cleaned_data_unique.csv", index=False)

# Save the resulting dataset to a CSV file
filtered_data_unique2.to_csv("filtered_cleaned_data_unique2.csv", index=False)

# Print the unique list of remaining countries
remaining_countries = filtered_data_unique["country"].unique()
print("Remaining countries after filtering:")
for country in sorted(remaining_countries):
    print(country)

Data shape after filtering excluded regions/categories: (4160, 130)



Filtered data unique 2:            country  year iso_code  population           gdp  \
21091     Vietnam  2002      VNM  80642304.0  2.506834e+11   
20756     Uruguay  2002      URY   3306446.0  3.725087e+10   
20800  Uzbekistan  2002      UZB  25579032.0  1.227578e+11   
21790    Zimbabwe  2002      ZWE  11984643.0  2.487248e+10   
21450       Yemen  2002      YEM  19660662.0  7.858648e+10   
...           ...   ...      ...         ...           ...   
12959     Namibia  2002      NAM   1888531.0  1.202187e+10   
12925     Myanmar  2002      MMR  46480236.0  1.015915e+11   
12801  Mozambique  2002      MOZ  18694948.0  2.102537e+10   
12677     Morocco  2002      MAR  29301820.0  1.513858e+11   
10567  Kyrgyzstan  2002      KGZ   5026646.0  1.617050e+10   

       biofuel_cons_change_pct  biofuel_cons_change_twh  \
21091                      NaN                      NaN   
20756                      NaN           

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/3174409095.py:17: UserWarning:

This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.



In [181]:
# After the data_2002_2021 filtering and before clustering_features definition

# Extract the last row for each country
latest_records = (
    data_2002_2021.sort_values("year", ascending=False)
    .drop_duplicates(subset=["country"], keep="first")
)

# Analyze missingness in all features
all_features_missingness = latest_records.isnull().sum().reset_index()
all_features_missingness.columns = ["Feature", "Missing Count"]

# Add the percentage of missing values
all_features_missingness["Missing Percentage"] = (
    all_features_missingness["Missing Count"] / len(latest_records) * 100
)

# Sort by missing percentage
all_features_missingness = all_features_missingness.sort_values(
    by="Missing Percentage", ascending=True  # Sort ascending to see complete features first
)

# Display the analysis
print("\nMissingness analysis for all features:")
print(all_features_missingness)

# Optionally, show features with zero missing values
complete_features = all_features_missingness[all_features_missingness["Missing Count"] == 0]
print("\nFeatures with complete data:")
print(complete_features)

# Save the analysis
all_features_missingness.to_csv("all_features_missingness_analysis.csv", index=False)


Missingness analysis for all features:
                          Feature  Missing Count  Missing Percentage
0                         country              0            0.000000
26             electricity_demand              0            0.000000
27  electricity_demand_per_capita              0            0.000000
28         electricity_generation              0            0.000000
36         fossil_elec_per_capita              0            0.000000
..                            ...            ...                 ...
23                coal_production            175           84.134615
22           coal_prod_per_capita            175           84.134615
21           coal_prod_change_twh            175           84.134615
20           coal_prod_change_pct            175           84.134615
73        nuclear_cons_change_pct            177           85.096154

[130 rows x 3 columns]

Features with complete data:
                           Feature  Missing Count  Missing Percentage
0       

In [182]:
# Then standardize other numerical features
numerical_features = data_2002_2021.select_dtypes(include=["number"]).columns
numerical_features = numerical_features.difference(["year"])

# Initialize a list to store standardization results for verification
standardization_results = []

# Manually standardize each numerical feature
for feature in numerical_features:
    if data_2002_2021[feature].isnull().all():
        print(f"Feature '{feature}' has only missing values; skipping standardization.")
        continue

    # Calculate mean and standard deviation
    feature_mean = data_2002_2021[feature].mean()
    feature_std = data_2002_2021[feature].std()

    # Avoid division by zero for constant features
    if feature_std == 0:
        print(f"Feature '{feature}' has zero standard deviation; setting standardized values to 0.")
        data_2002_2021[feature] = 0
    else:
        # Standardize the feature
        data_2002_2021[feature] = (data_2002_2021[feature] - feature_mean) / feature_std

    # Verify standardized results
    standardized_mean = data_2002_2021[feature].mean()
    standardized_std = data_2002_2021[feature].std()

    # Append results for verification
    standardization_results.append({
        "Feature": feature,
        "Original Mean": feature_mean,
        "Original StdDev": feature_std,
        "Standardized Mean": standardized_mean,
        "Standardized StdDev": standardized_std,
    })

# Create a DataFrame to display verification results
import pandas as pd
verification_df = pd.DataFrame(standardization_results)
print(verification_df)

# Calculate Non-NA Percentage for Each Country (Year >= 2000)
non_na_by_country_filtered = data_2002_2021.groupby("country").apply(
    lambda group: group.notnull().mean().mean() * 100  # Mean of non-NA values across all columns
).reset_index()

non_na_by_country_filtered.columns = ["Country", "Non-NA Percentage"]

# Sort by Non-NA Percentage in Descending Order
non_na_by_country_filtered_sorted = non_na_by_country_filtered.sort_values(
    by="Non-NA Percentage", ascending=False
)

# Display Results
print("Countries ranked by percentage of available data (2000 to 2021):")
print(non_na_by_country_filtered_sorted)

# Save to CSV for Further Analysis
non_na_by_country_filtered_sorted.to_csv("../datasets/energy/country_non_na_percentage_2000_to_2021.csv", index=False)

                     Feature  Original Mean  Original StdDev  \
0    biofuel_cons_change_pct      72.892820       372.216566   
1    biofuel_cons_change_twh       0.939974         4.986764   
2    biofuel_cons_per_capita     201.937839       306.135327   
3        biofuel_consumption      12.586782        47.385141   
4    biofuel_elec_per_capita      66.293803       200.907539   
..                       ...            ...              ...   
122     wind_elec_per_capita      85.178035       297.211769   
123         wind_electricity       3.085266        22.493015   
124   wind_energy_per_capita     455.647733       994.304735   
125          wind_share_elec       1.666793         5.234713   
126        wind_share_energy       1.366813         2.733539   

     Standardized Mean  Standardized StdDev  
0        -6.035187e-18                  1.0  
1        -6.728624e-18                  1.0  
2         9.122281e-17                  1.0  
3         1.990316e-17                  1.0  
4

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1143061158.py:45: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



# **Pre-processing of the Dataset**

## Overview
This preprocessing workflow focuses on preparing the **Our World in Data Energy Consumption Dataset** for clustering analysis by filtering relevant records, excluding non-country entities, handling missing values, and standardizing numerical features. These steps ensure the dataset is clean, consistent, and appropriately scaled for machine learning tasks.

---

### **Steps Performed**

#### **1. Data Filtering**
- **Purpose**: To focus on relevant, contemporary, and country-specific data for meaningful clustering results.
- **Actions**:
  - Filtered the dataset to include only records from the year **2000 to 2021**.
  - Excluded non-country entities such as:
    - Continents: Africa, Antarctica, Asia, Europe, North America, South America, and Oceania.
    - Regions: Middle East, Middle Africa, Western Africa, South and Central America, Pacific Islands, and Persian Gulf.
    - Groups: OECD, OPEC, ASEAN, and World.
    - Categories containing the word "income" or "territories."
- **Outcome**:
  - Reduced the dataset from **6659 rows** to **4809 rows** and retained **130 columns**, ensuring only valid country-level data remains.

---

#### **2. Handling Missing Values**
- **Purpose**: To identify and account for features with significant missing data.
- **Actions**:
  - Calculated the percentage of missing values for each column and each country.
  - Retained features with sufficient non-missing data for clustering analysis.
  - Identified countries with excessive missing data and excluded them to maintain data quality.
- **Outcome**:
  - Ensured the dataset includes countries and features with adequate data coverage for meaningful clustering.

---

#### **3. Standardization of Numerical Features**
- **Purpose**: To normalize numerical data, ensuring all features contribute equally to the clustering algorithm.
- **Actions**:
  - Selected all numerical features in the dataset for standardization, excluding the `year` column to preserve its interpretability.
  - For each feature:
    - Calculated its **mean** and **standard deviation**.
    - Transformed the feature to have a **mean of 0** and a **standard deviation of 1**.
    - Verified the results to ensure successful standardization.
- **Key Insights**:
  - Features such as `primary_energy_consumption`, `electricity_demand`, and `carbon_intensity_elec` showed significant variability before standardization.
  - Standardization results confirmed:
    - **Standardized Mean**: Approximated to 0 for all features.
    - **Standardized StdDev**: Exactly 1 for all features.

---

## Insights and Justifications

1. **Temporal Focus**:
   - Filtering records from **2000 to 2021** ensures the analysis reflects modern energy trends and policies.

2. **Exclusion of Non-Country Entities**:
   - Removing regions, continents, and ambiguous entities ensures the dataset is focused on valid country-level data, aligning with the clustering objectives.

3. **Data Completeness**:
   - Retaining features with adequate data ensures meaningful clustering without introducing noise from imputed or overly sparse features.

4. **Standardization**:
   - Standardizing numerical features eliminates the impact of differing scales (e.g., population measured in millions vs. carbon intensity in grams per kWh), ensuring each feature contributes equally to the clustering model.

---

## Summary
The preprocessing steps ensure the dataset is clean, scaled, and ready for clustering analysis. These actions align with the goal of creating robust clusters that accurately represent energy consumption, production, and environmental trends across countries.

In [183]:
# For the year 2000 dataset (filtered_data_unique2)
missing_data_country = filtered_data_unique2[
    filtered_data_unique2[['solar_electricity', 'solar_elec_per_capita', 
                          'oil_electricity', 'oil_elec_per_capita']].isnull().any(axis=1)
]

# Display the country and these features
print("Country missing these features in 2000:")
print(missing_data_country[['country', 'solar_electricity', 'solar_elec_per_capita', 
                           'oil_electricity', 'oil_elec_per_capita']])

Country missing these features in 2000:
Empty DataFrame
Columns: [country, solar_electricity, solar_elec_per_capita, oil_electricity, oil_elec_per_capita]
Index: []


# **WE ARE NOT DOING THIS ANYMORE** 


## **Energy Profile K-Means Clustering Analysis** 

## Goal
To cluster countries based on their energy development, consumption patterns, and environmental impact to identify three distinct groups of nations with similar energy profiles.

## Clustering Groups and Features

### 1. "High-Consuming, High-Carbon" Nations
Countries with high industrialization and fossil fuel dependence
- Features:
  * primary_energy_consumption (88.17%) - Overall energy needs
  * electricity_demand (83.09%) - Validates consumption level
  * fossil_electricity (86.39%) - Fossil fuel dependence
  * fossil_elec_per_capita (79.19%) - Individual fossil use
- Expected examples: USA, China

### 2. "High-Consuming, Low-Carbon" Nations
Developed countries with successful clean energy transition
- Features:
  * low_carbon_electricity (86.83%) - Clean energy scale
  * low_carbon_elec_per_capita (79.35%) - Validates clean energy adoption
  * renewables_share_elec (87.58%) - Transition progress
  * carbon_intensity_elec (82.67%) - System cleanliness
- Expected examples: France, Sweden

### 3. "Low-Consuming Economies"
Developing nations with lower energy consumption
- Features:
  * energy_per_capita (78.06%) - Development level
  * electricity_demand_per_capita (79.13%) - Access to electricity
  * per_capita_electricity (79.37%) - Validates per-person consumption
  * greenhouse_gas_emissions (83.09%) - Environmental impact
- Expected examples: Many African and South Asian nations

## Feature Selection Rationale
- All features have >78% data completeness
- Each cluster has equal representation (4 features)
- Includes both primary and validating metrics
- Balances absolute and per-capita measures
- Combines development and environmental indicators
- Avoids curse of dimensionality while maintaining robust clustering

# **C. Feature Extraction / Learning from Dataset**

In [184]:
# # Filter the dataset for data from the year 2000 and onward
# data_filtered = data[data["year"] >= 2000].copy()

# # Verify the filtered dataset
# print("Filtered dataset shape (year >= 2000):", data_filtered.shape)

# # Calculate the percentage of non-NA data for each column (year >= 2000)
# non_na_percentage_filtered = (data_filtered.notnull().sum() / len(data_filtered)) * 100

# # Convert to a DataFrame for better readability
# non_na_df_filtered = non_na_percentage_filtered.sort_values(ascending=False).reset_index()
# non_na_df_filtered.columns = ["Column", "Non-NA Percentage"]

# # Merge with the codebook to include additional information
# non_na_with_codebook_filtered = pd.merge(
#     non_na_df_filtered, 
#     codebook, 
#     left_on="Column", 
#     right_on="column",  # Adjust if codebook column names differ
#     how="left"
# )

# # Drop duplicate column name from the codebook
# non_na_with_codebook_filtered.drop(columns=["column"], inplace=True, errors="ignore")

# # Print the results
# print("Percentage of Non-NA Data for Each Column (year >= 2000, with Codebook Info):")
# print(non_na_with_codebook_filtered)

# # Save the merged data to a CSV file
# non_na_with_codebook_filtered.to_csv("../datasets/energy/non_na_percentage_with_codebook_2000_onward.csv", index=False)

In [185]:
# # Filter the dataset for data from the year 2000 and onward
# data_filtered = data[data["year"] >= 2000].copy()

# # Verify the filtered dataset
# print("Filtered dataset shape (year >= 2000):", data_filtered.shape)

# # Calculate Non-NA Percentage for Each Country (Year >= 2000)
# non_na_by_country_filtered = data_filtered.groupby("country").apply(
#     lambda group: group.notnull().mean().mean() * 100  # Mean of non-NA values across all columns
# ).reset_index()

# non_na_by_country_filtered.columns = ["Country", "Non-NA Percentage"]

# # Sort by Non-NA Percentage in Descending Order
# non_na_by_country_filtered_sorted = non_na_by_country_filtered.sort_values(
#     by="Non-NA Percentage", ascending=False
# )

# # Display Results
# print("Countries ranked by percentage of available data (year >= 2000):")
# print(non_na_by_country_filtered_sorted)

# # Save to CSV for Further Analysis
# non_na_by_country_filtered_sorted.to_csv("../datasets/energy/country_non_na_percentage_2000_onward.csv", index=False)

In [186]:
# Define Clustering Features
clustering_features = [
    "primary_energy_consumption",
    "electricity_demand",
    "fossil_electricity",
    "fossil_elec_per_capita",
    "low_carbon_electricity",
    "low_carbon_elec_per_capita",
    "renewables_share_elec",
    "carbon_intensity_elec",
    "energy_per_capita",
    "electricity_demand_per_capita",
    "per_capita_electricity",
    "greenhouse_gas_emissions",
    "year", # Exclude from clustering in processing step
]

# Ensure all selected features exist in the dataset
clustering_features = [feature for feature in clustering_features if feature in data_2002_2021.columns]
print(f"Selected features for clustering: {clustering_features}")

# Filter data for clustering features
data_clustering = data_2002_2021[["country"] + clustering_features].copy()
print(f"Dataset shape after selecting clustering features: {data_clustering.shape}")

# Check for Missing Values
missing_values = data_clustering.isnull().sum()
if missing_values.any():
    print("Warning: Missing values found in clustering features!")
    print(missing_values)
else:
    print("No missing values in the selected features.")

# Calculate the percentage of non-NA data for each clustering feature by country
country_feature_non_na = data_clustering.groupby("country")[clustering_features].apply(
    lambda group: group.notnull().mean() * 100
).reset_index()

# Reshape the data for better visualization (optional)
country_feature_non_na_long = country_feature_non_na.melt(
    id_vars="country", var_name="Feature", value_name="Non-NA Percentage"
)

# Display results
print("Percentage of available data for clustering features by country:")
print(country_feature_non_na_long)

# Define the threshold for minimum non-NA percentage
threshold = 80

# Calculate the average percentage of non-NA data for each country across clustering features
country_feature_non_na_mean = data_clustering.groupby("country")[clustering_features].apply(
    lambda group: group.notnull().mean().mean() * 100
).reset_index()

country_feature_non_na_mean.columns = ["country", "Average Non-NA Percentage"]

# Filter countries above the threshold
countries_above_threshold = country_feature_non_na_mean[
    country_feature_non_na_mean["Average Non-NA Percentage"] >= threshold
]

# Display results
print(f"Countries with data availability above {threshold}%:")
print(countries_above_threshold)

# Filter the dataset to include only countries above the threshold
filtered_data = data_clustering[data_clustering["country"].isin(countries_above_threshold["country"])]
print(f"Filtered dataset shape: {filtered_data.shape}")

Selected features for clustering: ['primary_energy_consumption', 'electricity_demand', 'fossil_electricity', 'fossil_elec_per_capita', 'low_carbon_electricity', 'low_carbon_elec_per_capita', 'renewables_share_elec', 'carbon_intensity_elec', 'energy_per_capita', 'electricity_demand_per_capita', 'per_capita_electricity', 'greenhouse_gas_emissions', 'year']
Dataset shape after selecting clustering features: (4160, 14)
country                           0
primary_energy_consumption       30
electricity_demand                0
fossil_electricity                0
fossil_elec_per_capita            0
low_carbon_electricity            0
low_carbon_elec_per_capita        0
renewables_share_elec             0
carbon_intensity_elec             0
energy_per_capita                30
electricity_demand_per_capita     0
per_capita_electricity            0
greenhouse_gas_emissions          0
year                              0
dtype: int64
Percentage of available data for clustering features by country:

In [187]:
# Analyze missingness for ALL features, but only for countries above threshold
all_features_missingness = filtered_data_unique[
    filtered_data_unique["country"].isin(countries_above_threshold["country"])
].isnull().sum().reset_index()

all_features_missingness.columns = ["Feature", "Missing Count"]

# Add the percentage of missing values
all_features_missingness["Missing Percentage"] = (
    all_features_missingness["Missing Count"] / len(countries_above_threshold) * 100
)

# Sort by missing percentage (ascending to see complete features first)
all_features_missingness = all_features_missingness.sort_values(
    by="Missing Percentage", ascending=True
)

# Display the analysis
print("\nMissingness analysis for all features (only for countries above threshold):")
print(all_features_missingness)

# Show features with zero missing values
complete_features = all_features_missingness[all_features_missingness["Missing Count"] == 0]
print("\nFeatures with complete data for selected countries:")
print(complete_features)

# Save the analysis
all_features_missingness.to_csv("all_features_missingness_analysis_filtered_countries.csv", index=False)




# Analyze missingness for ALL features, but only for countries above threshold, this is for countries at year 2000
all_features_missingness2 = filtered_data_unique2[
    filtered_data_unique2["country"].isin(countries_above_threshold["country"])
].isnull().sum().reset_index()

all_features_missingness2.columns = ["Feature", "Missing Count"]

# Add the percentage of missing values
all_features_missingness2["Missing Percentage"] = (
    all_features_missingness2["Missing Count"] / len(countries_above_threshold) * 100
)

# Sort by missing percentage (ascending to see complete features first)
all_features_missingness2 = all_features_missingness2.sort_values(
    by="Missing Percentage", ascending=True
)

# Display the analysis
print("\nMissingness analysis for all features (only for countries above threshold):")
print(all_features_missingness2)

# Show features with zero missing values
complete_features2 = all_features_missingness2[all_features_missingness2["Missing Count"] == 0]
print("\nFeatures with complete data for selected countries:")
print(complete_features2)

# Save the analysis
all_features_missingness2.to_csv("all_features_missingness_analysis_filtered_countries2.csv", index=False)


Missingness analysis for all features (only for countries above threshold):
                          Feature  Missing Count  Missing Percentage
0                         country              0            0.000000
26             electricity_demand              0            0.000000
27  electricity_demand_per_capita              0            0.000000
28         electricity_generation              0            0.000000
36         fossil_elec_per_capita              0            0.000000
..                            ...            ...                 ...
23                coal_production            175           84.134615
22           coal_prod_per_capita            175           84.134615
21           coal_prod_change_twh            175           84.134615
20           coal_prod_change_pct            175           84.134615
73        nuclear_cons_change_pct            177           85.096154

[130 rows x 3 columns]

Features with complete data for selected countries:
                  

In [188]:
# For the year 2000 dataset (filtered_data_unique2)
missing_data_country = filtered_data_unique2[
    filtered_data_unique2[['solar_electricity', 'solar_elec_per_capita', 
                          'oil_electricity', 'oil_elec_per_capita']].isnull().any(axis=1)
]

# Display the country and these features
print("Country missing these features in 2000:")
print(missing_data_country[['country', 'solar_electricity', 'solar_elec_per_capita', 
                           'oil_electricity', 'oil_elec_per_capita']])

Country missing these features in 2000:
Empty DataFrame
Columns: [country, solar_electricity, solar_elec_per_capita, oil_electricity, oil_elec_per_capita]
Index: []


In [189]:
# Count unique countries in filtered_data_unique
num_countries = len(filtered_data_unique['country'].unique())
print(f"Number of countries in filtered_data_unique: {num_countries}")

# Optionally, display the list of countries
print("\nList of countries:")
for country in sorted(filtered_data_unique['country'].unique()):
    print(country)

Number of countries in filtered_data_unique: 208

List of countries:
Afghanistan
Albania
Algeria
American Samoa
Angola
Antigua and Barbuda
Argentina
Armenia
Aruba
Australia
Austria
Azerbaijan
Bahamas
Bahrain
Bangladesh
Barbados
Belarus
Belgium
Belize
Benin
Bermuda
Bhutan
Bolivia
Bosnia and Herzegovina
Botswana
Brazil
British Virgin Islands
Brunei
Bulgaria
Burkina Faso
Burundi
Cambodia
Cameroon
Canada
Cape Verde
Cayman Islands
Chad
Chile
China
Colombia
Comoros
Congo
Cook Islands
Costa Rica
Cote d'Ivoire
Croatia
Cuba
Cyprus
Czechia
Democratic Republic of Congo
Denmark
Djibouti
Dominica
Dominican Republic
Ecuador
Egypt
El Salvador
Equatorial Guinea
Eritrea
Estonia
Eswatini
Ethiopia
Falkland Islands
Faroe Islands
Fiji
Finland
France
French Guiana
French Polynesia
Gabon
Gambia
Georgia
Germany
Ghana
Gibraltar
Greece
Greenland
Grenada
Guadeloupe
Guam
Guatemala
Guinea
Guinea-Bissau
Guyana
Haiti
Honduras
Hong Kong
Hungary
Iceland
India
Indonesia
Iran
Iraq
Ireland
Israel
Italy
Jamaica
Japan
Jord

In [190]:
# Count unique countries in filtered_data_unique
num_countries = len(filtered_data_unique2['country'].unique())
print(f"Number of countries in filtered_data_unique: {num_countries}")

# Optionally, display the list of countries
print("\nList of countries:")
for country in sorted(filtered_data_unique2['country'].unique()):
    print(country)

Number of countries in filtered_data_unique: 208

List of countries:
Afghanistan
Albania
Algeria
American Samoa
Angola
Antigua and Barbuda
Argentina
Armenia
Aruba
Australia
Austria
Azerbaijan
Bahamas
Bahrain
Bangladesh
Barbados
Belarus
Belgium
Belize
Benin
Bermuda
Bhutan
Bolivia
Bosnia and Herzegovina
Botswana
Brazil
British Virgin Islands
Brunei
Bulgaria
Burkina Faso
Burundi
Cambodia
Cameroon
Canada
Cape Verde
Cayman Islands
Chad
Chile
China
Colombia
Comoros
Congo
Cook Islands
Costa Rica
Cote d'Ivoire
Croatia
Cuba
Cyprus
Czechia
Democratic Republic of Congo
Denmark
Djibouti
Dominica
Dominican Republic
Ecuador
Egypt
El Salvador
Equatorial Guinea
Eritrea
Estonia
Eswatini
Ethiopia
Falkland Islands
Faroe Islands
Fiji
Finland
France
French Guiana
French Polynesia
Gabon
Gambia
Georgia
Germany
Ghana
Gibraltar
Greece
Greenland
Grenada
Guadeloupe
Guam
Guatemala
Guinea
Guinea-Bissau
Guyana
Haiti
Honduras
Hong Kong
Hungary
Iceland
India
Indonesia
Iran
Iraq
Ireland
Israel
Italy
Jamaica
Japan
Jord

In [191]:
data_2002_2021_sorted = data_2002_2021.sort_values("year", ascending=False)
print(data_2002_2021_sorted)

#save the data_2002_2021_sorted to a csv file
data_2002_2021_sorted.to_csv("data_2002_2021_sorted.csv", index=False)

#save the data_2002_2021 to a csv file
data_2002_2021.to_csv("data_2002_2021.csv", index=False)


          country  year iso_code  population       gdp  \
21809    Zimbabwe  2021      ZWE   -0.134479 -0.288240   
8750       Guyana  2021      GUY   -0.248661       NaN   
10070       Italy  2021      ITA    0.190627  0.759912   
9946       Israel  2021      ISR   -0.187804 -0.138249   
9822      Ireland  2021      IRL   -0.217224 -0.153047   
...           ...   ...      ...         ...       ...   
12959     Namibia  2002      NAM   -0.240513 -0.294996   
12925     Myanmar  2002      MMR    0.094703 -0.248866   
12801  Mozambique  2002      MOZ   -0.114171 -0.290359   
12677     Morocco  2002      MAR   -0.034435 -0.223221   
10567  Kyrgyzstan  2002      KGZ   -0.216922 -0.292860   

       biofuel_cons_change_pct  biofuel_cons_change_twh  \
21809                      NaN                      NaN   
8750                       NaN                      NaN   
10070                -0.183750                -0.069178   
9946                 -0.204064                -0.192103   
9822    

In [192]:
# List of features with no missing values
complete_features = [
    'country', 'electricity_generation', 'oil_electricity', 'per_capita_electricity',
    'solar_elec_per_capita', 'fossil_elec_per_capita', 'fossil_electricity',
    'oil_elec_per_capita', 'electricity_demand_per_capita', 'fossil_share_elec',
    'renewables_share_elec', 'net_elec_imports_share_demand', 'renewables_electricity',
    'renewables_elec_per_capita', 'net_elec_imports', 'low_carbon_elec_per_capita',
    'low_carbon_electricity', 'greenhouse_gas_emissions', 'electricity_demand',
    'solar_electricity', 'low_carbon_share_elec', 'year', 'population',
    'oil_share_elec', 'solar_share_elec', 'carbon_intensity_elec'
]

def check_complete_features(data, features):
    # Filter for years 2000-2021
    mask = (data['year'] >= 2000) & (data['year'] <= 2021)
    data_2002_2021 = data[mask]
    
    # Check for NA values
    na_counts = data_2002_2021[features].isna().sum()
    features_with_na = na_counts[na_counts > 0]
    
    # Check for zero values (excluding 'year', 'country')
    numeric_features = [f for f in features if f not in ['year', 'country']]
    zero_counts = data_2002_2021[numeric_features].eq(0).sum()
    features_with_zeros = zero_counts[zero_counts > 0]
    
    print("Features with NA values:")
    if len(features_with_na) > 0:
        print(features_with_na)
    else:
        print("None found")
        
    print("\nFeatures with zero values:")
    if len(features_with_zeros) > 0:
        for feature, count in features_with_zeros.items():
            print(f"{feature}: {count} zeros")
    else:
        print("None found")
        
    # If any zeros found, show which countries and years have them
    if len(features_with_zeros) > 0:
        print("\nDetailed zero value analysis:")
        for feature in features_with_zeros.index:
            zero_mask = data_2002_2021[feature] == 0
            if zero_mask.any():
                print(f"\n{feature} zeros found in:")
                zero_records = data_2002_2021[zero_mask][['country', 'year', feature]]
                print(zero_records)

# Run the check
check_complete_features(data_2002_2021_sorted, complete_features)

Features with NA values:
None found

Features with zero values:
None found


In [193]:
# Get list of features that have NA values (excluding 'country' and 'year')
features_with_na = [f for f in complete_features if f not in ['country', 'year']]

# Find rows with any NA values in these features
missing_data_countries = data_2002_2021_sorted[
    data_2002_2021_sorted[features_with_na].isnull().any(axis=1)
]

# Display the countries, years, and their NA values
print("Countries with missing values:")
print(missing_data_countries[['country', 'year'] + features_with_na])

# Get a summary of which countries have missing data
print("\nSummary of countries with missing data:")
missing_countries = missing_data_countries['country'].unique()
for country in missing_countries:
    years = missing_data_countries[missing_data_countries['country'] == country]['year']
    print(f"{country}: Missing data in years {list(years)}")

Countries with missing values:
Empty DataFrame
Columns: [country, year, electricity_generation, oil_electricity, per_capita_electricity, solar_elec_per_capita, fossil_elec_per_capita, fossil_electricity, oil_elec_per_capita, electricity_demand_per_capita, fossil_share_elec, renewables_share_elec, net_elec_imports_share_demand, renewables_electricity, renewables_elec_per_capita, net_elec_imports, low_carbon_elec_per_capita, low_carbon_electricity, greenhouse_gas_emissions, electricity_demand, solar_electricity, low_carbon_share_elec, population, oil_share_elec, solar_share_elec, carbon_intensity_elec]
Index: []

[0 rows x 26 columns]

Summary of countries with missing data:


In [194]:
# create new csv that has all countries from data_2002_2021 with only certain features
# List of features with no missing values
complete_features = [
    'country','year','population', 'electricity_generation', 'oil_electricity', 'per_capita_electricity',
    'solar_elec_per_capita', 'fossil_elec_per_capita', 'fossil_electricity',
    'oil_elec_per_capita', 'electricity_demand_per_capita', 'fossil_share_elec',
    'renewables_share_elec', 'net_elec_imports_share_demand', 'renewables_electricity',
    'renewables_elec_per_capita', 'net_elec_imports', 'low_carbon_elec_per_capita',
    'low_carbon_electricity', 'greenhouse_gas_emissions', 'electricity_demand',
    'solar_electricity', 'low_carbon_share_elec',
    'oil_share_elec', 'solar_share_elec', 'carbon_intensity_elec'
]

print(data_2002_2021.head())

# creating new csv
data_2002_2021_complete_features = data_2002_2021[complete_features]
data_2002_2021_complete_features.to_csv("complete_features_data_2002_2021.csv", index=False)


         country  year iso_code  population       gdp  \
126  Afghanistan  2002      AFG   -0.096841 -0.291503   
127  Afghanistan  2003      AFG   -0.084476 -0.290334   
128  Afghanistan  2004      AFG   -0.077647 -0.289686   
129  Afghanistan  2005      AFG   -0.071200 -0.288107   
130  Afghanistan  2006      AFG   -0.063443 -0.286404   

     biofuel_cons_change_pct  biofuel_cons_change_twh  \
126                      NaN                      NaN   
127                      NaN                      NaN   
128                      NaN                      NaN   
129                      NaN                      NaN   
130                      NaN                      NaN   

     biofuel_cons_per_capita  biofuel_consumption  biofuel_elec_per_capita  \
126                      NaN                  NaN                -0.329972   
127                      NaN                  NaN                -0.329972   
128                      NaN                  NaN                -0.329972   
12

# **Feature Engineering**

## Overview
This section focuses on preparing the dataset for clustering analysis. We select key features relevant to energy profiles for clustering. Countries with sufficient data availability have been identified for robust analysis.

---

### **Steps Performed**

#### **1. Evaluate Data Completeness**
- **Purpose**: To assess the availability of data at the column and country levels.
- **Steps**:
  - Calculated the percentage of non-NA values for each column.
  - Merged column-wise percentages with the codebook for clarity and saved the results for further review.
  - Calculated the average percentage of non-NA values for each country across all columns.
  - Identified and ranked countries by data completeness.
- **Outcome**: Data completeness results were saved and summarized:
  - Column-level non-NA percentages highlight feature reliability.
  - Country-level non-NA percentages identify countries with sufficient data coverage.

---

#### **2. Select Relevant Features for Clustering**
- **Purpose**: To ensure the clustering analysis focuses on features critical to understanding energy development, consumption patterns, and environmental impact.
- **Steps**:
  - Selected 12 key features based on domain knowledge and data availability:
    - Primary metrics (e.g., `primary_energy_consumption`, `electricity_demand`).
    - Validating metrics (e.g., `fossil_elec_per_capita`, `renewables_share_elec`).
    - Environmental indicators (e.g., `carbon_intensity_elec`, `greenhouse_gas_emissions`).
  - Verified that all selected features exist in the filtered dataset.
  - Extracted these features along with the `country` column to create a clustering dataset.
- **Outcome**: A subset of the dataset containing 12 clustering features and the `country` column was prepared for analysis.

---

#### **3. Identify Countries with Sufficient Data**
- **Purpose**: To ensure clustering is performed on countries with reliable data.
- **Steps**:
  - Calculated the percentage of non-NA data for each clustering feature by country.
  - Reshaped the results for better visualization and interpretation.
  - Calculated the average percentage of non-NA data for each country across all selected clustering features.
  - Defined a threshold of 80% data availability to filter countries with sufficient data.
  - Filtered the clustering dataset to include only these countries.
- **Outcome**: 
  - Countries meeting the threshold were identified and displayed.
  - A final filtered dataset, containing 12 clustering features for countries with >80% data availability, was created for further analysis.

---

## Insights
- The dataset from 2000 to 2021 provides a robust basis for clustering analysis, focusing on recent trends.
- Selected features capture critical aspects of energy development, consumption, and environmental impact.
- Filtering ensures clustering is performed on countries with high data completeness, reducing potential biases.
- The prepared dataset is now ready for clustering, with reliable features and sufficient coverage.

# **D. Processing of Dataset**

In [195]:
# import pandas as pd

# # Analyze missingness in the entire dataset
# data_missingness = filtered_data.isnull().sum().reset_index()
# data_missingness.columns = ["Feature", "Missing Count"]

# # Add the percentage of missing values
# data_missingness["Missing Percentage"] = (
#     data_missingness["Missing Count"] / len(filtered_data) * 100
# )

# # Sort by the highest missingness
# data_missingness = data_missingness.sort_values(by="Missing Percentage", ascending=False)

# # Display the analysis
# print("Missingness in the entire dataset:")
# print(data_missingness)

# # Check the distribution of years
# if "year" in filtered_data.columns:
#     year_distribution = filtered_data["year"].value_counts().reset_index()
#     year_distribution.columns = ["Year", "Count"]
#     print("\nYear distribution in the dataset:")
#     print(year_distribution)

# # Save the analysis to a CSV file
# data_missingness.to_csv("data_missingness_analysis.csv", index=False)

In [196]:
# import pandas as pd

# # Extract the last row for each country
# last_rows = filtered_data.groupby("country").tail(1)

# # Analyze missingness in the last rows
# last_row_missingness = last_rows.isnull().sum().reset_index()
# last_row_missingness.columns = ["Feature", "Missing Count"]

# # Add the percentage of missing values
# last_row_missingness["Missing Percentage"] = (
#     last_row_missingness["Missing Count"] / len(last_rows) * 100
# )

# # Sort by the highest missingness
# last_row_missingness = last_row_missingness.sort_values(by="Missing Percentage", ascending=False)

# # Display the analysis
# print("Missingness in the last row of each country:")
# print(last_row_missingness)

# # Check the years for the last rows
# if "year" in last_rows.columns:
#     years_in_last_rows = last_rows["year"].value_counts().reset_index()
#     years_in_last_rows.columns = ["Year", "Count"]
#     print("\nYears corresponding to the last row of each country:")
#     print(years_in_last_rows)

# # Save the analysis to a CSV file
# last_row_missingness.to_csv("last_row_missingness_analysis.csv", index=False)


# OLD! Comprehensive Clustering Analysis Breakdown

## 1. UPDATED Available Features After Processing
We have 26 high-quality features with complete data (no missing values or zeros) for years 2000-2021:

```python
complete_features = [
    'country', 'electricity_generation', 'oil_electricity', 'per_capita_electricity',
    'solar_elec_per_capita', 'fossil_elec_per_capita', 'fossil_electricity',
    'oil_elec_per_capita', 'electricity_demand_per_capita', 'fossil_share_elec',
    'renewables_share_elec', 'net_elec_imports_share_demand', 'renewables_electricity',
    'renewables_elec_per_capita', 'net_elec_imports', 'low_carbon_elec_per_capita',
    'low_carbon_electricity', 'greenhouse_gas_emissions', 'electricity_demand',
    'solar_electricity', 'low_carbon_share_elec', 'year', 'population',
    'oil_share_elec', 'solar_share_elec', 'carbon_intensity_elec'
]
```

## 2. Clustering Goal OUTDATED NOW

### Primary Objective
Identify distinct patterns in countries' energy development, efficiency, and sustainability profiles.

### Expected Outcomes

1. **High Efficiency, Clean Energy Countries**
   - Advanced economies with strong environmental policies
   - High per-capita metrics with significant renewable integration
   - Focus on sustainability and efficiency

2. **High Volume, Mixed Energy Countries**
   - Large economies with diverse energy sources
   - High total generation but moderate per-capita metrics
   - Balancing development with sustainability

3. **Developing Energy Systems**
   - Growing economies with evolving energy infrastructure
   - Lower per-capita metrics
   - Higher dependency on traditional energy sources

## 3. Selected Features for Clustering (14 Total Features)

### A. Energy Mix Ratios (4 features)
```python
mix_features = [
    'fossil_share_elec',      # NEW - total fossil fuel share
    'renewables_share_elec',  # NEW - total renewables share
    'low_carbon_share_elec',  # NEW - total low carbon share
    'oil_share_elec',        # NEW - replaces oil_dependency
    'solar_share_elec'       # NEW - replaces solar_share
]
```

- **Why**: Shows energy strategy and priorities regardless of country size
- **Helps identify**: Energy transition progress and policy choices

### B. Per Capita Metrics (6 features)
```python
per_capita_features = [
'electricity_demand_per_capita',
'per_capita_electricity',
'fossil_elec_per_capita',
'renewables_elec_per_capita',
'low_carbon_elec_per_capita',
'solar_elec_per_capita'
]
```

- **Why**: Shows development level and efficiency independent of country size
- **Helps identify**: Living standards and energy infrastructure maturity

### C. Scale Indicators (3 features)
```python
scale_features = [
    'electricity_generation',
    'electricity_demand',
    'net_elec_imports',
    'net_elec_imports_share_demand'  # NEW - indicates energy independence
]
```

- **Why**: Shows overall energy system size and self-sufficiency
- **Helps identify**: Economic scale and energy independence

### D. Environmental Impact and Effeciency (2 feature)
```python
environmental_features = [
    'carbon_intensity_elec',  # NEW - emissions per unit of electricity
    'greenhouse_gas_emissions'
]
```

- **Why**: Direct measure of environmental impact
- **Helps identify**: Efficiency of energy production and use

## 4. Features Not Used and Why

1. `country` and `year`
   - Identifiers, not meaningful for clustering

2. `population`
   - Already reflected in per-capita metrics
   - Could skew results due to vast differences
   - Better used for normalization than clustering

3. Raw total values of specific sources (when ratio is used instead)
   - `renewables_electricity`
   - `fossil_electricity`
   - `oil_electricity`
   - `solar_electricity`
   - **Why**: Ratios provide more meaningful comparisons across different sized economies

## 5. Additional Considerations

### Data Preprocessing Needs
- Feature scaling (due to different units)
- Calculation of ratio features
- Potential outlier handling

### Expected Challenges
1. Wide range of country sizes
2. Different development stages
3. Various geographical and resource constraints

### Validation Approach
- Check if clusters align with known economic groupings
- Verify temporal stability (consistent across years)
- Ensure interpretability of results

## **Back to Feature Engineering Real Quick**

In [197]:
# we have the following data frame with all data we are working with
print(data_2002_2021_complete_features.head())

         country  year  population  electricity_generation  oil_electricity  \
126  Afghanistan  2002   -0.096841               -0.217240        -0.316660   
127  Afghanistan  2003   -0.084476               -0.216823        -0.311756   
128  Afghanistan  2004   -0.077647               -0.217073        -0.312982   
129  Afghanistan  2005   -0.071200               -0.217011        -0.312982   
130  Afghanistan  2006   -0.063443               -0.216844        -0.316660   

     per_capita_electricity  solar_elec_per_capita  fossil_elec_per_capita  \
126               -0.729435              -0.308173               -0.733351   
127               -0.728225              -0.308173               -0.731785   
128               -0.729486              -0.308173               -0.732565   
129               -0.729476              -0.308173               -0.732668   
130               -0.729138              -0.308173               -0.732429   

     fossil_electricity  oil_elec_per_capita  ...  net_e

In [198]:
# goal is to remoce feautres that we are not using for clustering and create 


# **Attemp at Final Comprehensive Clustering Analysis Breakdown**

## 1. UPDATED Available Features After Processing
We have 26 high-quality features with complete data (no missing values or zeros) for years 2000-2021:

```python
complete_features = [
    'country', 'electricity_generation', 'oil_electricity', 'per_capita_electricity',
    'solar_elec_per_capita', 'fossil_elec_per_capita', 'fossil_electricity',
    'oil_elec_per_capita', 'electricity_demand_per_capita', 'fossil_share_elec',
    'renewables_share_elec', 'net_elec_imports_share_demand', 'renewables_electricity',
    'renewables_elec_per_capita', 'net_elec_imports', 'low_carbon_elec_per_capita',
    'low_carbon_electricity', 'greenhouse_gas_emissions', 'electricity_demand',
    'solar_electricity', 'low_carbon_share_elec', 'year', 'population',
    'oil_share_elec', 'solar_share_elec', 'carbon_intensity_elec'
]
```

# Clustering Goal

## Primary Objective

Identify distinct patterns in countries' energy systems by focusing on:
- Energy mix composition
- System efficiency and environmental impact
- Development status

## Expected Outcomes

### 1. High Efficiency, Clean Energy Countries

**Characteristics:**
- Advanced economies with strong environmental policies
- High per-capita electricity consumption with significant renewable integration
- Low carbon intensity and greenhouse gas emissions

**Focus:** Sustainability and efficiency

### 2. High Volume, Mixed Energy Countries

**Characteristics:**
- Large economies with diverse energy sources
- High total electricity generation but moderate per-capita metrics
- Balancing development with sustainability

**Focus:** Economic scale and energy diversity

### 3. Developing Energy Systems

**Characteristics:**
- Growing economies with evolving energy infrastructure
- Lower per-capita electricity consumption
- Higher dependency on traditional energy sources like oil

**Focus:** Infrastructure development and energy transition

## Selected Features for Clustering

### A. Energy Mix Ratios (5 features)

```python
mix_features = [
    'fossil_share_elec',      # Total fossil fuel share
    'renewables_share_elec',  # Total renewables share
    'low_carbon_share_elec',  # Total low carbon share
    'oil_share_elec',         # Oil share in electricity
    'solar_share_elec'        # Solar share in electricity
]
```

**Why:** These features show the energy strategy and priorities of a country, regardless of its size.

**Helps identify:** Progress in energy transition and policy choices.

### B. Per Capita Metrics (5 features)

```python
per_capita_features = [
    'electricity_demand_per_capita',
    'per_capita_electricity',
    'fossil_elec_per_capita',
    'renewables_elec_per_capita',
    'low_carbon_elec_per_capita'
]
```

**Why:** These metrics indicate the development level and efficiency of a country, independent of its size.

**Helps identify:** Living standards and maturity of energy infrastructure.

### C. Scale Indicators (3 features)

```python
scale_features = [
    'electricity_generation',
    'electricity_demand',
    'net_elec_imports_share_demand'  # Indicates energy independence
]
```

**Why:** These features show the overall size of the energy system and self-sufficiency.

**Helps identify:** Economic scale and energy independence.

### D. Environmental Impact and Efficiency (2 features)

```python
environmental_features = [
    'carbon_intensity_elec',  # Emissions per unit of electricity
    'greenhouse_gas_emissions'
]
```

**Why:** These are direct measures of environmental impact.

**Helps identify:** Efficiency of energy production and use.

## Implementation Plan

1. **Data Preparation:**
   - Filter and clean the dataset to include only the selected features
   - Standardize the features to ensure comparability

2. **Clustering Analysis:**
   - Use clustering algorithms (e.g., K-Means) to identify patterns
   - Evaluate the clusters for interpretability and distinctiveness

3. **Validation and Interpretation:**
   - Validate the clusters against known economic and energy profiles
   - Interpret the results to derive actionable insights

## Features Not Used and Reasons

### Excluded Features

1. **country and year**
   - **Reason:** These are identifiers and do not provide meaningful information for clustering. They are used for labeling and temporal analysis but not for clustering.

2. **population**
   - **Reason:** While population is important, its effects are already captured in per-capita metrics. Including it directly could skew results due to vast differences in country sizes.

3. **Raw Total Values** (oil_electricity, solar_electricity, etc.)
   - **Reason:** These raw total values are less informative than their corresponding share or per-capita metrics. Shares and per-capita values provide a normalized view that is more comparable across countries.

4. **Redundant Per-Capita Metrics**
   - **Reason:** While these per-capita metrics are useful, they are redundant when we already include broader per-capita metrics like per_capita_electricity and electricity_demand_per_capita. The broader metrics capture overall consumption patterns more effectively.

5. **net_elec_imports**
   - **Reason:** This feature is less informative on its own compared to net_elec_imports_share_demand, which provides a relative measure of energy independence.

6. **electricity_demand**
   - **Reason:** Similar to electricity_generation, but less informative when we already have electricity_demand_per_capita and electricity_generation as scale indicators.

## Summary

The decision to exclude these features is based on the need to:
- Avoid redundancy and focus on the most informative metrics
- Use normalized or relative measures (e.g., shares, per-capita) for better comparability
- Ensure the clustering analysis remains interpretable and focused on key aspects of energy systems

**Goal:** Create clusters that are both meaningful and actionable, capturing the essence of each country's energy profile without unnecessary complexity.


In [199]:
# Getting ready to implement clustering tasks
# first we have to get data frame only with features we are using for clustering

# Define the features to use for clustering
selected_features = [
    'fossil_share_elec', 'renewables_share_elec', 'low_carbon_share_elec',
    'oil_share_elec', 'solar_share_elec', 'electricity_demand_per_capita',
    'per_capita_electricity', 'fossil_elec_per_capita', 'renewables_elec_per_capita',
    'low_carbon_elec_per_capita', 'electricity_generation', 'net_elec_imports_share_demand',
    'carbon_intensity_elec', 'greenhouse_gas_emissions'
]

# Retain the country label for interpretation
country_labels = data_2002_2021_complete_features['country']

# Filter the data to include only the selected features
clustering_data = data_2002_2021_complete_features[selected_features]



In [208]:
import pandas as pd
import plotly.express as px
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA

# Define the 5-year periods
periods = [(2002, 2006), (2007, 2011), (2012, 2016), (2017, 2021)]

# Initialize a list to store results for each period
all_period_results = []

# Initialize a list to store results for each period
cluster_counts = []

# Process each 5-year period
for start_year, end_year in periods:
    # Filter data for the current period
    period_data = data_2002_2021_complete_features[
        (data_2002_2021_complete_features['year'] >= start_year) &
        (data_2002_2021_complete_features['year'] <= end_year)
    ]
    
    # Average the features for each country
    averaged_data = period_data.groupby('country')[selected_features].mean().reset_index()
    
    # Perform K-Means clustering
    kmeans = KMeans(n_clusters=3, random_state=42)
    averaged_data['Cluster'] = kmeans.fit_predict(averaged_data[selected_features])

    # Analyze cluster centroids
    centroids = pd.DataFrame(kmeans.cluster_centers_, columns=selected_features)
    print(f"Cluster centroids for period {start_year}-{end_year}:")
    print(centroids)
    print()
    
    # Analyze feature distribution within each cluster
    for cluster in range(3):
        cluster_data = averaged_data[averaged_data['Cluster'] == cluster]
        print(f"Feature distribution for Cluster {cluster} ({start_year}-{end_year}):")
        print(cluster_data.describe())
        print()
    
    # # Perform PCA for visualization
    # pca = PCA(n_components=2)
    # pca_result = pca.fit_transform(averaged_data[selected_features])
    # averaged_data['PCA1'] = pca_result[:, 0]
    # averaged_data['PCA2'] = pca_result[:, 1]

    # Perform PCA with 3 components
    pca = PCA(n_components=3)
    pca_result = pca.fit_transform(averaged_data[selected_features])
    averaged_data['PCA1'] = pca_result[:, 0]
    averaged_data['PCA2'] = pca_result[:, 1]
    averaged_data['PCA3'] = pca_result[:, 2]

    # Create a 3D scatter plot with Plotly
    fig = px.scatter_3d(
        averaged_data,
        x='PCA1',
        y='PCA2',
        z='PCA3',
        color='Cluster',
        hover_data=['country'],
        title=f'3D Clusters of Countries Based on Energy Features ({start_year}-{end_year})',
        labels={'PCA1': 'Principal Component 1', 'PCA2': 'Principal Component 2', 'PCA3': 'Principal Component 3'}
    )

    # Show the plot
    fig.show()

    # Check the explained variance ratio
    explained_variance = pca.explained_variance_ratio_
    print(f"Explained variance by the first two components: {explained_variance.sum() * 100:.2f}%")
    
    # Store the results
    all_period_results.append((start_year, end_year, averaged_data))

    # Count the number of countries in each cluster
    cluster_count = averaged_data['Cluster'].value_counts().sort_index()
    cluster_counts.append((start_year, end_year, cluster_count))

    # # Visualize the clusters for the current period
    # fig = px.scatter(
    #     averaged_data,
    #     x='PCA1',
    #     y='PCA2',
    #     color='Cluster',
    #     hover_data=['country'],
    #     title=f'Clusters of Countries Based on Energy Features ({start_year}-{end_year})',
    #     labels={'PCA1': 'Principal Component 1', 'PCA2': 'Principal Component 2'}
    # )
    
    # # Show the plot
    # fig.show()

# Print the number of countries in each cluster for each period
for start_year, end_year, counts in cluster_counts:
    print(f"Period {start_year}-{end_year}:")
    for cluster, count in counts.items():
        print(f"  Cluster {cluster}: {count} countries")
    print()

Explained variance by the first two components: 77.15%


Explained variance by the first two components: 77.80%


Explained variance by the first two components: 79.52%


Explained variance by the first two components: 71.18%
Period 2002-2006:
  Cluster 0: 128 countries
  Cluster 1: 10 countries
  Cluster 2: 70 countries

Period 2007-2011:
  Cluster 0: 68 countries
  Cluster 1: 69 countries
  Cluster 2: 71 countries

Period 2012-2016:
  Cluster 0: 127 countries
  Cluster 1: 76 countries
  Cluster 2: 5 countries

Period 2017-2021:
  Cluster 0: 133 countries
  Cluster 1: 74 countries
  Cluster 2: 1 countries



In [204]:
## stuff

In [ ]:
## below

In [ ]:
## is 

In [ ]:
## old

In [200]:
# Implementing k-means clustering
from sklearn.cluster import KMeans

# Initialize the KMeans model
kmeans = KMeans(n_clusters=3, random_state=42)

# Fit the model to the data
kmeans.fit(clustering_data)

# Add the cluster labels and country labels to the original DataFrame
data_2002_2021_complete_features['Cluster'] = kmeans.labels_
data_2002_2021_complete_features['Country'] = country_labels

# Save the clustered data to a new CSV
data_2002_2021_complete_features.to_csv("clustered_data_2002_2021.csv", index=False)

# Print the first few rows of the clustered data
print(data_2002_2021_complete_features[['Country', 'Cluster']].head())

         Country  Cluster
126  Afghanistan        1
127  Afghanistan        1
128  Afghanistan        1
129  Afghanistan        1
130  Afghanistan        1


/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1807420880.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1807420880.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [201]:
import plotly.express as px
from sklearn.decomposition import PCA

# Load the clustered data
# data_2002_2021_complete_features = pd.read_csv("clustered_data_2002_2021.csv")

# Define the features used for clustering
selected_features = [
    'fossil_share_elec', 'renewables_share_elec', 'low_carbon_share_elec',
    'oil_share_elec', 'solar_share_elec', 'electricity_demand_per_capita',
    'per_capita_electricity', 'fossil_elec_per_capita', 'renewables_elec_per_capita',
    'low_carbon_elec_per_capita', 'electricity_generation', 'net_elec_imports_share_demand',
    'carbon_intensity_elec', 'greenhouse_gas_emissions'
]

# Perform PCA to reduce dimensionality to 2D for visualization
pca = PCA(n_components=2)
pca_result = pca.fit_transform(data_2002_2021_complete_features[selected_features])

# Add PCA results to the DataFrame
data_2002_2021_complete_features['PCA1'] = pca_result[:, 0]
data_2002_2021_complete_features['PCA2'] = pca_result[:, 1]

# Create a scatter plot with Plotly
fig = px.scatter(
    data_2002_2021_complete_features,
    x='PCA1',
    y='PCA2',
    color='Cluster',
    hover_data=['Country'],
    title='Clusters of Countries Based on Energy Features',
    labels={'PCA1': 'Principal Component 1', 'PCA2': 'Principal Component 2'}
)

# Show the plot
fig.show()

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1309585932.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1309585932.py:22: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [202]:
# Load the complete features data
data_2002_2021_complete_features = pd.read_csv("complete_features_data_2002_2021.csv")

# Print column names to verify
print("Column names in the DataFrame:", data_2002_2021_complete_features.columns)

Column names in the DataFrame: Index(['country', 'year', 'population', 'electricity_generation',
       'oil_electricity', 'per_capita_electricity', 'solar_elec_per_capita',
       'fossil_elec_per_capita', 'fossil_electricity', 'oil_elec_per_capita',
       'electricity_demand_per_capita', 'fossil_share_elec',
       'renewables_share_elec', 'net_elec_imports_share_demand',
       'renewables_electricity', 'renewables_elec_per_capita',
       'net_elec_imports', 'low_carbon_elec_per_capita',
       'low_carbon_electricity', 'greenhouse_gas_emissions',
       'electricity_demand', 'solar_electricity', 'low_carbon_share_elec',
       'oil_share_elec', 'solar_share_elec', 'carbon_intensity_elec'],
      dtype='object')


In [203]:
import pandas as pd
import plotly.express as px
from sklearn.cluster import KMeans

# Define the features used for clustering
selected_features = [
    'fossil_share_elec', 'renewables_share_elec', 'low_carbon_share_elec',
    'oil_share_elec', 'solar_share_elec', 'electricity_demand_per_capita',
    'per_capita_electricity', 'fossil_elec_per_capita', 'renewables_elec_per_capita',
    'low_carbon_elec_per_capita', 'electricity_generation', 'net_elec_imports_share_demand',
    'carbon_intensity_elec', 'greenhouse_gas_emissions'
]

# Initialize a DataFrame to store cluster results
cluster_results = pd.DataFrame()

# Perform clustering for each year
for year in data_2002_2021_complete_features['year'].unique():
    # Filter data for the current year
    year_data = data_2002_2021_complete_features[data_2002_2021_complete_features['year'] == year]
    
    # Perform K-Means clustering
    kmeans = KMeans(n_clusters=3, random_state=42)
    year_data['Cluster'] = kmeans.fit_predict(year_data[selected_features])
    
    # Append results to the cluster_results DataFrame
    cluster_results = pd.concat([cluster_results, year_data[['country', 'year', 'Cluster']]])

# Filter for a specific region or subset of countries
# Example: Filter for countries in Europe (replace with actual country names or criteria)
european_countries = ['Germany', 'France', 'United Kingdom', 'Italy', 'Spain']
filtered_results = cluster_results[cluster_results['country'].isin(european_countries)]

# Visualize cluster transitions over time for the filtered countries
fig = px.line(
    filtered_results,
    x='year',
    y='Cluster',
    color='country',
    title='Cluster Transitions Over Time for Selected Countries',
    labels={'Cluster': 'Cluster Label', 'year': 'Year'}
)

# Show the plot
fig.show()

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1583998609.py:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1583998609.py:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/6c/tdhnd2xn4f1f_xq3h1r39xn40000gn/T/ipykernel_78763/1583998609.py:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th